## Upload dos arquivos

Nos blocos de código abaixo devem ser fornecidos (carregados) o arquivo de dataset (.csv) contendo os dados de polaridade e localização (latitude e longitude) dos tweets e o arquivo *GeoJSON* com os formatos dos estados do Brasil (**brazil-states.geojson** obtido em https://github.com/codeforamerica/click_that_hood/blob/master/public/data/brazil-states.geojson).

Na célula abaixo, escreva o nome do arquivo de dataset sem a extensão .csv

**PS.:** Basta modificar o valor no formulário que o código executará automaticamente.

In [29]:
# Upload dos arquivos
from google.colab import files
uploaded = files.upload()
for fn in uploaded.keys():
  print('Arquivo "{name}" with length {length} bytes'.format(
      name=fn, length=len(uploaded[fn])))

Saving Haddad2000.csv to Haddad2000.csv
Arquivo "Haddad2000.csv" with length 368634 bytes


In [0]:
#@title Nome do arquivo de dados sem a extensão .csv { display-mode: "form", run: "auto" }

file_name = 'Haddad2000' #@param {type:"string"}

## Instalação e *import* dos módulos

In [0]:
# Instalando dependências
!pip install folium shapely

In [0]:
import folium
from folium.plugins import HeatMap
import json
import pandas as pd
from branca.colormap import linear
from shapely.geometry import shape, Point

## Leitura e limpeza dos dados

A célula abaixo puramente lê o arquivo .csv fornecido para um **pandas.DataFrame** e imprime seu cabeçalho e informações.

In [32]:
tweets = pd.read_csv(file_name + '.csv', sep=';')
display(tweets.head())
display(tweets.info())

Unnamed: 0                                              texto  polarity  \
0           0  Haddad: 'Não tenham medo. Nós estaremos aqui. ...  -0.60000   
1           1  @Haddad_Fernando Até 2022, Presidente Haddad! ...   0.80000   
2           2  Pessoal, existe um abismo bem grande cultural ...   0.12619   
3           3  @Brayantmenna @R_BALLBOA @morenofla5 @Haddad_F...   0.00000   
4           4  No primeiro discurso após derrota, Haddad pede...   0.25000   

   subjectivity                   location  Latitude  Longitude  
0      0.900000                     Paraná -31.72631  -60.53147  
1      1.000000     Rio de Janeiro, Brazil -22.91216  -43.17501  
2      0.319048                    Barueri -23.50428  -46.84461  
3      0.000000              Milão, Itália  45.46796    9.18178  
4      0.333333  Brasil, Paraná, Curitiba, -25.43998  -49.27654

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2120 entries, 0 to 2119
Data columns (total 7 columns):
Unnamed: 0      2120 non-null int64
texto           2120 non-null object
polarity        2120 non-null float64
subjectivity    2120 non-null float64
location        2120 non-null object
Latitude        2072 non-null float64
Longitude       2072 non-null float64
dtypes: float64(4), int64(1), object(2)
memory usage: 116.0+ KB


None

É possível notar que há uma coluna desnecessária: **`'Unnamed: 0'`**, vamos excluí-la e também descartar as entradas com tweets sem coordenadas de localização.

In [33]:
# desconsideraremos os tweets sem localização
tweets = tweets.drop('Unnamed: 0', axis='columns')
tweets = tweets.dropna(subset=['Latitude', 'Longitude'])
tweets.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2072 entries, 0 to 2119
Data columns (total 6 columns):
texto           2072 non-null object
polarity        2072 non-null float64
subjectivity    2072 non-null float64
location        2072 non-null object
Latitude        2072 non-null float64
Longitude       2072 non-null float64
dtypes: float64(4), object(2)
memory usage: 113.3+ KB


# Plotagem dos mapas

## Colormap

Para visualização dos tweets no map, será utilizado como coloração o valor de polaridade sentimental, valor que vai de -1 (ruim:  <font color="red">vermelho</font>) e 1 (bom:  <font color="blue">azul</font>)

In [9]:
# colormap vermelho (ruim) para azul (bom)
colormap = linear.RdBu_03.scale(-1, 1)
colormap

## Mapa com pontos

Para visualização de todos os tweets localizáveis no mapa, são utilizados marcadores circulares com a coloração indicativa de sua polaridade. É possível clicar em um ponto para visualizar o valor de polaridade.

In [34]:
# put your code here
map_points = folium.Map(
    location=[0.0000000, 25.000000],
    zoom_start=3,
    tiles='Stamen Terrain',
)

for i, tweet in tweets.iterrows():
  folium.CircleMarker([tweet['Latitude'],tweet['Longitude']],
                      popup='polaridade: %f'%(tweet['polarity']),
                      radius=8, 
                      color='#000000',
                      weight=1,
                      fill=True, 
                      fill_color=colormap(tweet['polarity']),
                      fill_opacity=1.0).add_to(map_points)
  
  colormap.caption = 'Polaridade dos tweets'
  colormap.add_to(map_points)
  
map_points.save(file_name + '_points.html')
display(map_points)

## Mapas de calor

O código abaixo gera três mapas de calor de acordo com densidade de tweets. O primeiros dos mapas mostra todos os tweets, o segundo os tweets com avaliação de polaridade bastante positiva (> 0.5) e, por fim, o terceiro mostra os tweets com polaridade bastante negativa (< -0.5)

In [35]:
# Mapas de calor com todos os tweets e os mais exacerbados (polaridade > 0.5 e < -0.5)

m = []
for i in range(3):
  m.append(folium.Map(
      location=[0.0000000, 25.000000],
      zoom_start=3,
      tiles='Stamen Terrain',
  ))

total_data = tweets.loc[:, ['Latitude', 'Longitude', 'polarity']].values
HeatMap(total_data).add_to(m[0])
                        
positive_data = tweets.loc[tweets['polarity'] > 0.5, ['Latitude', 'Longitude', 'polarity']].values
HeatMap(positive_data).add_to(m[1])
                        
negative_data = tweets.loc[tweets['polarity'] < -0.5, ['Latitude', 'Longitude', 'polarity']].values
HeatMap(negative_data).add_to(m[2])

m[0].save(file_name + '_heat_total.html')
m[1].save(file_name + '_heat_positive.html')
m[2].save(file_name + '_heat_megative.html')

display(m[0])
display(m[1])
display(m[2])

### Carregamento do arquivo GeoJSON

In [0]:
#Fonte: https://github.com/codeforamerica/click_that_hood/blob/master/public/data/brazil-states.geojson
geo_json_data = json.load(open('brazil-states.geojson'))

## Distribuição dos tweets por estado brasileiro

A célula de código abaixo gera um dicionário com todos os estados e sua forma geográfica, obtidos do arquivo *GeoJSON*. E, em seguida, itera pelo *DataFrame* dos tweets, para que estes sejam contabilizados no seu estado federativo (basicamente checa se o ponto geográfico está dentro do território do estado, e adiciona seu valor à estatística).

Logo após, é mostrado o *DataFrame* obtido a partir do dicionario.

In [36]:
# Monta um dicionário com todos os estados mais exterior
states = {}

for state in geo_json_data['features']:
    states[state['properties']['name']] = {
        'shape': shape(state['geometry']),
        'count':0,
        'sum':0,
        'mean':0,
        'min':0,
        'max':0
    }
exterior = {'shape': None, 'count':0, 'sum':0, 'mean':0, 'min':0, 'max':0}
    
    
# Agora, para todos os tweets...
for i, tweet in tweets.iterrows():
  #gera um ponto (x, y) com o local (long, lat) do tweet
  tweet_local = Point(tweet['Longitude'], tweet['Latitude'])
  
  #checa se a localização do tweet está dentro de algum dos estados brasileiros
  for name, state in states.items():
    if state['shape'].contains(tweet_local):
      state['count'] += 1
      state['sum'] += tweet['polarity']
      state['mean'] = state['sum'] / state['count']
      state['min'] = min(tweet['polarity'], state['min'])
      state['max'] = max(tweet['polarity'], state['max'])
      break
  #se não estiver, vai para contagem do exterior
  else:
    exterior['count'] += 1
    exterior['sum'] += tweet['polarity']
    exterior['mean'] = exterior['sum'] / exterior['count']
    exterior['min'] = min(tweet['polarity'], exterior['min'])
    exterior['max'] = max(tweet['polarity'], exterior['max'])

states['Exterior'] = exterior

states_df = pd.DataFrame(states).drop(['shape', 'sum'], axis='index').transpose()
display(states_df)

count   max         mean       min
Acre                    3   0.1    0.0333333         0
Alagoas                11   0.5     0.122297      -0.6
Amapá                   5     1     0.327273         0
Amazonas               13     1   -0.0329545      -0.6
Bahia                  57   0.8    0.0588462      -0.9
Ceará                  34     1    0.0886029      -0.5
Distrito Federal       47   0.9     0.112373        -1
Espírito Santo         33     1     0.021158      -0.6
Exterior              483     1    0.0321382        -1
Goiás                  32   0.6    0.0215732      -0.8
Maranhão               21     1     0.159921 -0.466667
Mato Grosso           200     1    0.0594762        -1
Mato Grosso do Sul     22   0.5   -0.0346681      -0.7
Minas Gerais          120     1   0.00586735 -0.714286
Paraná                 82   0.8    0.0456716      -0.7
Paraíba                21   0.5  0.000992063      -0.6
Pará                   31  0.55   -0.0193548     -0.75
Pernambuco             52   0.7    0.0524444      -0.7
Piauí                  11  0.58    0.0701515 -0.166667
Rio Grande do Norte    12   0.5    0.0666667         0
Rio Grande do Sul      99     1    0.0224213        -1
Rio de Janeiro        221     1    0.0483724        -1
Rondônia                9   0.8   0.00960648 -0.651042
Roraima                 2   0.5         0.25         0
Santa Catarina         73   0.8  -0.00396033      -0.8
Sergipe                10   0.5    0.0795313         0
São Paulo             362     1     0.046055        -1
Tocantins               6   0.8       0.1375         0

### Colormap adaptado

Como a utilização do colormap anterior (com interpolação de -1.0 a 1.0) geraria um mapa com coloração clara e com pouco contrastre, o código abaixo determina o maior valor absoluto entre a menor e maior média de polaridade dos estados e gera um colormap com a interpolação do negativo deste valor ao positivo. Desta forma obtem-se um melhor contraste do mapa.

In [37]:
#determina o maior valor absoluto das médias para gerar um colormap com maior contraste
edge_val = max(abs(states_df['mean'].min()), abs(states_df['mean'].max()))

enhanced_colormap = linear.RdBu_03.scale(-edge_val, edge_val)
enhanced_colormap

### Mapa coroplético

O código abaixo gera um mapa com os estados coloridos de acordo com a polaridade média dos seus tweets, utilizando a escala colorimétrica (colormap) gerada acima.

In [38]:
map_choropleth = folium.Map(
    location=[-16.000000, -55.000000],
    zoom_start=5,
    tiles='Stamen Terrain'
)

# Gera o mapa do Brasil
folium.GeoJson(geo_json_data,
               name='Média dos sentimentos dos tweets por estado',
               style_function=lambda state: {
                   'fillColor': '#d3d3d3' if states[state['properties']['name']]['count'] == 0
                   else enhanced_colormap(states[state['properties']['name']]['mean']),
                   'color': 'black',
                   'weight': 1,
                   'dashArray': '5, 5',
                   'fillOpacity': 0.9,
               }).add_to(map_choropleth)

enhanced_colormap.caption = 'Polaridade dos tweets'
enhanced_colormap.add_to(map_choropleth)

map_choropleth.save(file_name + '_choropleth.html')
display(map_choropleth)

## Download dos arquivos dos mapas

Todos os códigos que geram mapas salvaram um arquivo .html para cada mapa. Se estiver executando este ***notebook*** no [Google Colab](https://colab.research.google.com/), estes arquivos podem ser baixados na aba *Files* do painel lateral.